In [2]:
from transformers import RobertaModel
from transformers import RobertaTokenizer
import csv 
import matplotlib.pyplot as plt

# Moral Stories

In [ ]:
data = data.explode('tag')

from sentence_transformers import SentenceTransformer
model = SentenceTransformer('all-MiniLM-L6-v2')

with open('outputMoralStories3.tsv', 'w', newline='') as f_output:
    tsv_output = csv.writer(f_output, delimiter='\t')
    a = list(range(0,384))
    #a.append("moral")
    a.append("class")
    tsv_output.writerow(a)
    
    for index, row in data.iterrows():
        print(index)
        b = model.encode(row['moral'].replace("Moral:", "")).tolist()
        #b.append(row['moral'].replace("Moral:", "").replace(" ", "_"))
        b.append(row['tag'])
        tsv_output.writerow(b)

In [ ]:


tokenizer = RobertaTokenizer.from_pretrained('roberta-large')
model = RobertaModel.from_pretrained('roberta-large')


with open('output.tsv', 'w', newline='') as f_output:
    tsv_output = csv.writer(f_output, delimiter='\t')
    a = list(range(0,1024))
    a.append("class")
    tsv_output.writerow(a)
    for w in morals:
        token_ids = tokenizer.encode(w)
        tokens = [tokenizer._convert_id_to_token(idx) for idx in token_ids]

        token_ids = torch.tensor(token_ids).unsqueeze(0)
        output = model(token_ids)[0].squeeze()

        cls_out = output[0]
        b = cls_out.tolist()
        b.append(w.replace(" ", "_"))
        tsv_output.writerow(b)

# Aesop Stories

In [3]:
from transformers import AutoTokenizer, TFAutoModelForSequenceClassification
import tensorflow as tf
import pandas
import torch
import csv

In [4]:
# Classification using ROBERTA

data= pandas.read_csv("C:/Users/Thiloshon/PycharmProjects/analogical-transfer-learning/aesop_morals_com_annotated_singleclass.csv")

a = data['tag'].value_counts()
a = a[a > 3]
keys = list(a.keys())

data_filt = data[data.tag.apply(lambda x: x in keys)]

labels = list(data_filt['tag'])
morals = list(data_filt['moral'])
morals = [mor.replace("Moral:", "") for mor in morals]

stories = list(data_filt['story'])

data_filt

Unnamed: 0                                                url  \
1             1  https://www.litscape.com/author/Aesop/The_Ants...   
2             2  https://www.litscape.com/author/Aesop/The_Ass_...   
3             3  https://www.litscape.com/author/Aesop/The_Ass_...   
4             4  https://www.litscape.com/author/Aesop/The_Ass_...   
8             8  https://www.litscape.com/author/Aesop/The_Ass_...   
..          ...                                                ...   
224         224  https://www.litscape.com/author/Aesop/The_Wolf...   
226         226  https://www.litscape.com/author/Aesop/The_Wolf...   
230         230  https://www.litscape.com/author/Aesop/The_Wolf...   
234         234  https://www.litscape.com/author/Aesop/The_Wolf...   
235         235  https://www.litscape.com/author/Aesop/The_Wolv...   

                               title  \
1       The Ants and the Grasshopper   
2             The Ass and His Driver   
3          The Ass and His Purchaser   
4             The Ass and His Shadow   
8               The Ass and the Wolf   
..                               ...   
224           The Wolf and the Crane   
226           The Wolf and the Horse   
230           The Wolf and the Sheep   
234  The Wolf, The Goat, And The Kid   
235         The Wolves and the Sheep   

                                                 story  \
1    THE ANTS were employing a fine winter's day in...   
2    AN ASS, being driven along a high road, sudden...   
3    A MAN wished to purchase an Ass, and agreed wi...   
4    A TRAVELER hired an Ass to convey him to a dis...   
8    AN ASS, feeding in a meadow, saw a Wolf approa...   
..                                                 ...   
224  A WOLF, having a bone stuck in his throat, hir...   
226  A WOLF coming out of a field of oats met a Hor...   
230  A WOLF, being sick and maimed, called to a She...   
234  AS AN OLD GOAT was going forth to pasture, she...   
235  WHY SHOULD there always be this implacable war...   

                                                 moral    category  \
1                          Moral:Idleness brings want.        life   
2           Moral:The perverse generally come to harm.        life   
3        Moral:A man is known by the company he keeps.        life   
4    Moral:In quarreling about the shadow, we often...        life   
8                        Moral:Everyone has his trade.        life   
..                                                 ...         ...   
224  Moral:In serving the wicked, expect no reward,...        life   
226  Moral:Men of evil reputation, when they perfor...        life   
230  Moral:Hypocritical speeches are easily seen th...        life   
234            Moral:Two sureties are better than one.  motivation   
235                 Moral:Change not friends for foes.        life   

             tag  
1           lazy  
2         danger  
3        friends  
4     worthiness  
8     worthiness  
..           ...  
224  consequence  
226  true-nature  
230  true-nature  
234        greed  
235      friends  

[141 rows x 7 columns]

In [5]:
data_filt.to_csv('aesop_morals_com_commontags.csv', encoding='utf-8')

In [10]:
data= pandas.read_csv("C:/Users/Thiloshon/PycharmProjects/analogical-transfer-learning/aesop_morals_com_commontags - edit.csv")


labels = list(data['tag'])
morals = list(data['moral'])

stories = list(data['story'])


116

In [11]:
# Tuning model

categories=sorted(list(set(labels))) #set will return the unique different entries
n_categories=len(categories)
n_elements = len(morals)

def indicize_labels(labels):
    """Transforms string labels into indices"""
    indices=[]
    for j in range(len(labels)):
        for i in range(n_categories):
            if labels[j]==categories[i]:
                indices.append(i)
    return indices

tokenizer = AutoTokenizer.from_pretrained("roberta-base") #Tokenizer
inputs = tokenizer(morals[0], padding=True, truncation=True, return_tensors='tf') #Tokenized text

print(inputs["input_ids"])

tokens = tokenizer.convert_ids_to_tokens(inputs["input_ids"])
print(tokens)

indices=indicize_labels(labels)

print("pp")
print(indices)


#s = pandas.Series(indices)
#indices = pandas.get_dummies(s)

dataset=tf.data.Dataset.from_tensor_slices((dict(inputs), indices)) #Create a tensorflow dataset
#train test split, we use 10% of the data for validation
val_data_size=int(0.1*n_elements)
val_ds=dataset.take(val_data_size).batch(8, drop_remainder=True) 
train_ds=dataset.skip(val_data_size).batch(8, drop_remainder=True)
train_ds = train_ds.prefetch(buffer_size=tf.data.experimental.AUTOTUNE)

tokens=tokenizer(morals[0:3], padding=True, truncation=True)['input_ids']
for i in range(3):
  print('Input:',morals[i])
  print('Subword tokenization:',tokenizer.tokenize(morals[i]))
  print('Indices:', tokens[i])


model = TFAutoModelForSequenceClassification.from_pretrained("roberta-base", num_labels=n_categories)
model.compile(
    optimizer=tf.keras.optimizers.Adam(learning_rate=1e-5, clipnorm=1.),
    loss=tf.keras.losses.SparseCategoricalCrossentropy(from_logits=True),
    metrics=[tf.metrics.SparseCategoricalAccuracy(),tf.keras.metrics.SparseTopKCategoricalAccuracy(k=3, name='Sparse_Top_3_Categorical_Accuracy')],
    )
    
history=model.fit(train_ds, validation_data=val_ds, epochs=12, verbose=1)

plt.plot(history.history['loss'])
plt.plot(history.history['val_loss'])
plt.ylabel('model loss')
plt.xlabel('epoch')
plt.legend(['train', 'test'], loc='best')
plt.savefig('train_history.png')
plt.show()

tf.Tensor([[    0 24523  9314   531  1057 45492   219     4     2]], shape=(1, 9), dtype=int32)


TypeError: only size-1 arrays can be converted to Python scalars

In [25]:
with open('output_tuned_roberta.tsv', 'w', newline='') as f_output:
    tsv_output = csv.writer(f_output, delimiter='\t')
    toks = tokenizer(morals, padding=True, truncation=True, return_tensors='tf')
    outputs = model(toks, output_hidden_states= True)
    hidden_states = outputs['hidden_states']
    embedding_output = hidden_states[0]

    

    avg_vector = tf.reduce_mean(embedding_output, 1)
    
    print(avg_vector.shape)
    
    for i in range(0, 141):
        
        b = avg_vector[i].numpy().tolist()
    
        print(b)
        tsv_output.writerow(b)

(141, 768)
[0.17850136756896973, 0.1483902633190155, -0.2192193865776062, -0.1883808672428131, -0.17711660265922546, 0.15408955514431, -0.14410658180713654, -0.1705540120601654, -0.20206274092197418, -0.23937250673770905, -0.17681966722011566, 0.05898740887641907, 0.30383285880088806, -0.32003676891326904, 0.13199813663959503, 0.3254767060279846, 0.19727611541748047, -0.24669675529003143, -0.30853351950645447, 0.2809348702430725, 0.22151386737823486, 0.282554566860199, -0.03799299895763397, 0.2866145670413971, 0.18347065150737762, 0.26089736819267273, 0.0989408940076828, 0.24951761960983276, 0.1321399211883545, -0.3159738779067993, 0.2074195295572281, 0.12163390219211578, -0.28699514269828796, 0.1729177087545395, -0.29526185989379883, 0.8743511438369751, 0.1789466142654419, 0.25042837858200073, -0.29470840096473694, -0.18823207914829254, 0.3735593557357788, -0.11574871093034744, -0.22939707338809967, -0.16767966747283936, -0.18726570904254913, 0.1963423788547516, -0.14948253333568573, 

[0.14142610132694244, 0.11062654852867126, -0.19962634146213531, -0.1597631573677063, -0.1643216907978058, 0.1154879629611969, -0.10889283567667007, -0.1519872546195984, -0.18618139624595642, -0.19733743369579315, -0.12050498276948929, 0.11451356112957001, 0.24175336956977844, -0.23485642671585083, 0.12891344726085663, 0.3128708600997925, 0.19321571290493011, -0.18963173031806946, -0.28842300176620483, 0.1882386952638626, 0.161717489361763, 0.2496187388896942, -0.025803182274103165, 0.210804283618927, 0.19201119244098663, 0.1835702359676361, 0.05623606964945793, 0.28003498911857605, 0.1275823414325714, -0.2941749393939972, 0.11596762388944626, 0.08670086413621902, -0.24372026324272156, 0.18878212571144104, -0.28432247042655945, 0.7581371068954468, 0.12553724646568298, 0.17971961200237274, -0.1322702318429947, -0.14042030274868011, 0.29713305830955505, -0.10718347132205963, -0.17734311521053314, -0.08792558312416077, -0.16114932298660278, 0.21984675526618958, -0.13269299268722534, 0.220

[0.1286298781633377, -0.005808612331748009, -0.01438479870557785, 0.02479330450296402, -0.10573296248912811, -0.036026664078235626, -0.04796382412314415, -0.022060947492718697, -0.11389344185590744, -0.07621277868747711, -0.006569317076355219, 0.030277851969003677, -0.04563159495592117, -0.03116684779524803, 0.1322120726108551, 0.07561850547790527, 0.023103142157197, -0.09946899861097336, -0.20096078515052795, 0.09899257123470306, 0.12334346771240234, 0.07007438689470291, -0.11189469695091248, 0.028264334425330162, 0.012957590632140636, 0.0083708381280303, 0.09010772407054901, 0.09770158678293228, 0.003696301020681858, -0.013303393498063087, 0.064382404088974, 0.028466152027249336, 0.0019534353632479906, 0.051880016922950745, -0.1264757513999939, 0.1840236783027649, 0.051386769860982895, 0.02682030200958252, 0.16144205629825592, -0.0579134076833725, 0.15120892226696014, 0.056603990495204926, 0.009894843213260174, 0.011291014030575752, -0.058824051171541214, 0.08982416242361069, -0.0341

[0.12482985854148865, 0.08703677356243134, -0.14437425136566162, -0.08618199825286865, -0.16168266534805298, 0.05271059274673462, -0.11486195027828217, -0.10800859332084656, -0.12302225083112717, -0.2514500617980957, -0.08661442995071411, 0.022243846207857132, 0.18915502727031708, -0.2009243220090866, 0.12152182310819626, 0.1937643438577652, 0.10034172981977463, -0.10909799486398697, -0.17869819700717926, 0.11745502054691315, 0.15646052360534668, 0.2386593222618103, -0.06884019821882248, 0.15737523138523102, 0.1129908412694931, 0.17714186012744904, 0.04183086380362511, 0.190404012799263, 0.08192511647939682, -0.23509207367897034, 0.1344902366399765, 0.08192983269691467, -0.14835043251514435, 0.09979164600372314, -0.23683302104473114, 0.570128858089447, 0.16488225758075714, 0.11855562776327133, -0.09447398036718369, -0.12196552753448486, 0.22611451148986816, -0.06321932375431061, -0.10178536921739578, -0.08261990547180176, -0.08979925513267517, 0.1509520411491394, -0.06356113404035568, 

In [18]:
# Creating embeddings


#inputs = tokenizer(morals[0], return_tensors="tf")
#print(inputs)
#print("Embedding layer : hidden_states[0].shape ", avg_vector.shape) 

with open('output_tuned_roberta.tsv', 'w', newline='') as f_output:
    tsv_output = csv.writer(f_output, delimiter='\t')
    for idx, w in enumerate(morals):
        
        #input_ids = tf.constant(tokenizer.encode(w))[None, :]
        toks = tokenizer(w, padding=True, truncation=True, return_tensors='tf')
        outputs = model(toks, output_hidden_states= True)
        hidden_states = outputs['hidden_states']
        embedding_output = hidden_states[0]
        
        print(embedding_output.shape)
        
        avg_vector = tf.reduce_mean(embedding_output, 1)
        b = avg_vector.numpy().tolist()[0]
        tsv_output.writerow(b)
        
with open('output_tuned_roberta_metadata.tsv', 'w', newline='') as f_output:
    tsv_output = csv.writer(f_output, delimiter='\t')
    a = list(range(0,768))
    a.append("class")
    tsv_output.writerow(a)
    for idx, w in enumerate(morals):
        a = list(range(0,768))
        a.append(labels[idx])
        #b.append(w.replace(" ", "_") + "::" + labels[idx])
        #b.append(labels[idx])
        tsv_output.writerow(a)

(1, 7, 768)
(1, 9, 768)
(1, 12, 768)
(1, 16, 768)
(1, 7, 768)
(1, 11, 768)
(1, 41, 768)
(1, 11, 768)
(1, 9, 768)
(1, 20, 768)
(1, 23, 768)
(1, 12, 768)
(1, 18, 768)
(1, 14, 768)
(1, 10, 768)
(1, 13, 768)
(1, 14, 768)
(1, 15, 768)
(1, 15, 768)
(1, 10, 768)
(1, 12, 768)
(1, 14, 768)
(1, 11, 768)
(1, 10, 768)
(1, 16, 768)
(1, 20, 768)
(1, 7, 768)
(1, 8, 768)
(1, 7, 768)
(1, 16, 768)
(1, 15, 768)
(1, 18, 768)
(1, 17, 768)
(1, 11, 768)
(1, 21, 768)
(1, 17, 768)
(1, 17, 768)
(1, 13, 768)
(1, 8, 768)
(1, 14, 768)
(1, 20, 768)
(1, 22, 768)
(1, 14, 768)
(1, 15, 768)
(1, 11, 768)
(1, 10, 768)
(1, 17, 768)
(1, 8, 768)
(1, 14, 768)
(1, 18, 768)
(1, 7, 768)
(1, 12, 768)
(1, 12, 768)
(1, 13, 768)
(1, 13, 768)
(1, 16, 768)
(1, 18, 768)
(1, 13, 768)
(1, 23, 768)
(1, 10, 768)
(1, 14, 768)
(1, 9, 768)
(1, 12, 768)
(1, 15, 768)
(1, 14, 768)
(1, 12, 768)
(1, 12, 768)
(1, 13, 768)
(1, 17, 768)
(1, 28, 768)
(1, 14, 768)
(1, 25, 768)
(1, 14, 768)
(1, 14, 768)
(1, 13, 768)
(1, 10, 768)
(1, 15, 768)
(1, 12, 76

In [42]:
# USING MEAN POOLING

from transformers import AutoTokenizer, AutoModel
import torch


#Mean Pooling - Take attention mask into account for correct averaging
def mean_pooling(model_output, attention_mask):
    token_embeddings = model_output[0] #First element of model_output contains all token embeddings
    input_mask_expanded = attention_mask.unsqueeze(-1).expand(token_embeddings.size()).float()
    sum_embeddings = torch.sum(token_embeddings * input_mask_expanded, 1)
    sum_mask = torch.clamp(input_mask_expanded.sum(1), min=1e-9)
    return sum_embeddings / sum_mask



#Sentences we want sentence embeddings for
sentences = morals

#Load AutoModel from huggingface model repository
tokenizer = AutoTokenizer.from_pretrained("sentence-transformers/all-mpnet-base-v2")
model = AutoModel.from_pretrained("sentence-transformers/all-mpnet-base-v2")

#Tokenize sentences
encoded_input = tokenizer(sentences, padding=True, truncation=True, max_length=512, return_tensors='pt')

#Compute token embeddings
with torch.no_grad():
    model_output = model(**encoded_input)

#Perform pooling. In this case, mean pooling
sentence_embeddings = mean_pooling(model_output, encoded_input['attention_mask'])

In [48]:
with open('aesop_embedding_sentence_pooled.tsv', 'w', newline='') as f_output:
    tsv_output = csv.writer(f_output, delimiter='\t')
    
    for index, row in enumerate(sentence_embeddings):
        
        b = row.tolist()
        print(b)
        tsv_output.writerow(b)
        
        
with open('aesop_embedding_sentence_pooled_meta.tsv', 'w', newline='') as f_output:
    tsv_output = csv.writer(f_output, delimiter='\t')
    a = list(range(0,384))
    a.append("class")
    tsv_output.writerow(a)
    
    for index, row in enumerate(labels):
        a = list(range(0,384))
        a.append(labels[index])
        tsv_output.writerow(a)

[0.018121842294931412, 0.2928832471370697, -0.011364094913005829, -0.05818593502044678, 0.044669635593891144, 0.027851911261677742, -0.20368275046348572, 0.049154020845890045, 0.07644060999155045, 0.11845993995666504, 0.047761376947164536, 0.14308691024780273, 0.023143041878938675, -0.0879552811384201, 0.0413278229534626, 0.07816911488771439, 0.026145102456212044, 0.012546700425446033, -0.014925912953913212, 0.07933741807937622, 0.005581776145845652, 0.04122051224112511, 0.15825067460536957, -0.021099871024489403, 0.058728236705064774, 0.02977151609957218, 0.13251301646232605, 0.012320982292294502, -0.05874381586909294, 0.08401261270046234, 0.06020098924636841, 0.16990065574645996, 0.13224577903747559, -0.042215313762426376, 5.222818344918778e-06, -0.06189765781164169, 0.0725468248128891, -0.009746870025992393, -0.11230786144733429, 0.020207839086651802, 0.08767670392990112, 0.10734409093856812, 0.13073840737342834, -0.009285411797463894, -0.11566203832626343, 0.1622128039598465, -0.04

[-0.02246515080332756, 0.10430435091257095, -0.008236630819737911, 0.1990586370229721, -0.17582792043685913, -0.07452815771102905, 0.08070683479309082, -0.04263598471879959, 0.002636440098285675, -0.06426011025905609, -0.08631373196840286, -0.11416548490524292, -0.04118260741233826, -0.05934500694274902, -0.052375759929418564, 0.1078575849533081, 0.13999728858470917, 0.03839407488703728, 0.17535990476608276, -0.10727815330028534, 0.11017326265573502, 0.10501391440629959, -0.018968550488352776, -0.008722640573978424, -0.12580478191375732, -0.15110664069652557, 0.02581678330898285, 0.08779451251029968, 0.01643131859600544, 0.10844890773296356, -0.05272321030497551, 0.016134822741150856, -0.12067203223705292, 0.06367316097021103, 4.614795216184575e-06, 0.1039576604962349, -0.038053903728723526, -0.02090267464518547, 0.00221138633787632, -0.0876014232635498, -0.024088822305202484, 0.07347910106182098, -0.00012433243682608008, 0.09978199750185013, -0.06587900221347809, 0.09284964203834534, 

In [ ]:
# USING SENTENCE TRANFORMERS, untuned

import csv

from sentence_transformers import SentenceTransformer
model = SentenceTransformer('all-MiniLM-L6-v2')

with open('aesop_embedding_sentence_untuned.tsv', 'w', newline='') as f_output:
    tsv_output = csv.writer(f_output, delimiter='\t')
    
    for index, row in enumerate(morals):
        print(index)
        b = model.encode(row).tolist()
        tsv_output.writerow(b)
        
        
with open('aesop_embedding_sentence_untuned_meta.tsv', 'w', newline='') as f_output:
    tsv_output = csv.writer(f_output, delimiter='\t')
    a = list(range(0,384))
    a.append("class")
    tsv_output.writerow(a)
    
    for index, row in enumerate(labels):
        a = list(range(0,384))
        a.append(labels[index])
        tsv_output.writerow(a)

In [29]:
data_filt

Unnamed: 0                                                url  \
1             1  https://www.litscape.com/author/Aesop/The_Ants...   
2             2  https://www.litscape.com/author/Aesop/The_Ass_...   
3             3  https://www.litscape.com/author/Aesop/The_Ass_...   
4             4  https://www.litscape.com/author/Aesop/The_Ass_...   
8             8  https://www.litscape.com/author/Aesop/The_Ass_...   
..          ...                                                ...   
224         224  https://www.litscape.com/author/Aesop/The_Wolf...   
226         226  https://www.litscape.com/author/Aesop/The_Wolf...   
230         230  https://www.litscape.com/author/Aesop/The_Wolf...   
234         234  https://www.litscape.com/author/Aesop/The_Wolf...   
235         235  https://www.litscape.com/author/Aesop/The_Wolv...   

                               title  \
1       The Ants and the Grasshopper   
2             The Ass and His Driver   
3          The Ass and His Purchaser   
4             The Ass and His Shadow   
8               The Ass and the Wolf   
..                               ...   
224           The Wolf and the Crane   
226           The Wolf and the Horse   
230           The Wolf and the Sheep   
234  The Wolf, The Goat, And The Kid   
235         The Wolves and the Sheep   

                                                 story  \
1    THE ANTS were employing a fine winter's day in...   
2    AN ASS, being driven along a high road, sudden...   
3    A MAN wished to purchase an Ass, and agreed wi...   
4    A TRAVELER hired an Ass to convey him to a dis...   
8    AN ASS, feeding in a meadow, saw a Wolf approa...   
..                                                 ...   
224  A WOLF, having a bone stuck in his throat, hir...   
226  A WOLF coming out of a field of oats met a Hor...   
230  A WOLF, being sick and maimed, called to a She...   
234  AS AN OLD GOAT was going forth to pasture, she...   
235  WHY SHOULD there always be this implacable war...   

                                                 moral    category  \
1                          Moral:Idleness brings want.        life   
2           Moral:The perverse generally come to harm.        life   
3        Moral:A man is known by the company he keeps.        life   
4    Moral:In quarreling about the shadow, we often...        life   
8                        Moral:Everyone has his trade.        life   
..                                                 ...         ...   
224  Moral:In serving the wicked, expect no reward,...        life   
226  Moral:Men of evil reputation, when they perfor...        life   
230  Moral:Hypocritical speeches are easily seen th...        life   
234            Moral:Two sureties are better than one.  motivation   
235                 Moral:Change not friends for foes.        life   

             tag  
1           lazy  
2         danger  
3        friends  
4     worthiness  
8     worthiness  
..           ...  
224  consequence  
226  true-nature  
230  true-nature  
234        greed  
235      friends  

[141 rows x 7 columns]

In [39]:
# Moral similarity with  SENTENCE TRANSFORMERS

from sentence_transformers import SentenceTransformer, util

model = SentenceTransformer('all-MiniLM-L6-v2')


#Compute embeddings
embeddings = model.encode(morals, convert_to_tensor=True)

#Compute cosine-similarities for each sentence with each other sentence
cosine_scores = util.cos_sim(embeddings, embeddings)

#Find the pairs with the highest cosine similarity scores
pairs = []
for i in range(len(cosine_scores)-1):
    for j in range(i+1, len(cosine_scores)):
        pairs.append({'index': [i, j], 'score': cosine_scores[i][j]})

#Sort scores in decreasing order
pairs = sorted(pairs, key=lambda x: x['score'], reverse=True)

for pair in pairs:     
    i, j = pair['index']
    print("{} \t\t {} \t\t Score: {:.4f}".format(morals[i], morals[j], pair['score']))
    print("\n")

Our insignificance is often the cause of our safety. 		 What is safety to one is not always safety to another. 		 Score: 0.6804


Flattery is a dangerous weapon in the hands of the enemy. 		 Flattery is not a proof of admiration. 		 Score: 0.6478


He who listens to flattery is not wise, for it has no good purpose 		 Flattery is a dangerous weapon in the hands of the enemy. 		 Score: 0.6430


He who listens to flattery is not wise, for it has no good purpose 		 Flattery is not a proof of admiration. 		 Score: 0.6346


Misfortune tests the sincerity of friends. 		 It shows an evil disposition to take advantage of a friend in distress. 		 Score: 0.6054


By too much attention to danger, we may fall victims to it. 		 Better a little in safety, than an abundance surrounded by danger. 		 Score: 0.6053


Distance exaggerates dangers. 		 Better a little in safety, than an abundance surrounded by danger. 		 Score: 0.5948


Our insignificance is often the cause of our safety. 		 Better a little

He who will steal a part will steal the whole. 		 The greedy man and the miser cannot enjoy their gains. 		 Score: 0.3396


Kindness to the ungrateful and the vicious is thrown away. 		 Those who try to entrap others are sometimes caught by their own schemes. 		 Score: 0.3396


Kindness to the ungrateful and the vicious is thrown away. 		 Those who neglect their old friends for the sake of new ones, are rightly served if they lose both. 		 Score: 0.3395


We should never look so high as to miss seeing the things that are around us.  		 Distance exaggerates dangers. 		 Score: 0.3395


Those who practice cunning must expect to suffer by it. 		 No one is too weak to do good. 		 Score: 0.3390


Happy is the man who learns from the misfortunes of others. 		 Evil companions bring more hurt than profit. 		 Score: 0.3386


Kindness to the ungrateful and the vicious is thrown away. 		 By endeavoring to please everybody, one succeeds in pleasing nobody. 		 Score: 0.3386


We are encouraged by se



He who will steal a part will steal the whole. 		 Let every one stick to his own element. 		 Score: 0.2917


It shows an evil disposition to take advantage of a friend in distress. 		 By too much attention to danger, we may fall victims to it. 		 Score: 0.2916


A man is known by the company he keeps. 		 He who will steal a part will steal the whole. 		 Score: 0.2916


In injuring others we are apt to receive greater injury. 		 The vices we teach may be practiced against us. 		 Score: 0.2916


One story is good, till another is told. 		 Inconsiderate and ill-matched alliances generally end in ruin; and the man who compasses the destruction of his neighbor is often caught in his own snare. 		 Score: 0.2914


A man who can strike from a distance is no pleasant neighbor. 		 Distance exaggerates dangers. 		 Score: 0.2913


The greedy man and the miser cannot enjoy their gains. 		 Let every one stick to his own element. 		 Score: 0.2911


Much wants more, and loses all. 		 Some men despis

Everyone has his trade. 		 He who seeks to injure others often injures only himself. 		 Score: 0.2592


Everyone to his taste: one man's meat is another man's poison, and one mans poison is another man's meat; what is rejected by one person may be valued very highly by another. 		 They who assue a character will betray themselves by their actions. 		 Score: 0.2591


Everyone to his taste: one man's meat is another man's poison, and one mans poison is another man's meat; what is rejected by one person may be valued very highly by another. 		 Those who stir up enmities are not to be trusted. 		 Score: 0.2590


No one should be blamed for his infirmities. 		 If men had all they wished, they would be often ruined. 		 Score: 0.2590


He who seeks to injure others often injures only himself. 		 By endeavoring to please everybody, one succeeds in pleasing nobody. 		 Score: 0.2589


We should not wait till a person is dead, to give him our respect. 		 They who assue a character will betray the

Incentive spurs effort. 		 He who slights his friends when they are not needed must not expect them to serve him when he needs them. 		 Score: 0.2383


Men often fall into the trap which they prepare for others. 		 He who once begins to tell falsehoods is obliged to tell others to make them appear true, and, sooner or later, they will get him into trouble. 		 Score: 0.2383


By endeavoring to please everybody, one succeeds in pleasing nobody. 		 Do nothing without a regard to the consequences. 		 Score: 0.2382


Do not attempt too much at once. 		 If you wish to do a service, do it right. 		 Score: 0.2382


No one should be blamed for his infirmities. 		 He who offers bribes needs watching, for his intentions are not honest. 		 Score: 0.2382


Flattery is not a proof of admiration. 		 He who offers bribes needs watching, for his intentions are not honest. 		 Score: 0.2381


Those who suffer most cry out the least. 		 Evil companions bring more hurt than profit. 		 Score: 0.2381


If wo

...

Fine feathers don't make fine birds. 		 Unlawful acts to escape trials only increase our troubles. 		 Score: 0.1183


The same measures will not suit all circumstances. 		 Those who practice cunning must expect to suffer by it. 		 Score: 0.1182


A man is known by the company he keeps. 		 No disguise will hide one's true character. 		 Score: 0.1182


Avoid even appearances of danger. 		 It is too late to whet the sword when the trumpet sounds to draw it. 		 Score: 0.1182


Cure a boaster by putting his words to the test. 		 Danger sometimes comes from a source that is least suspected. 		 Score: 0.1182


He who once begins to tell falsehoods is obliged to tell others to make them appear true, and, sooner or later, they will get him into trouble. 		 Our mere anticipations of life outrun its realities. 		 Score: 0.1181


There is always some vulnerable part in the strongest armor. 		 Those who neglect their old friends for the sake of new ones, are rightly served if they lose both. 		 Sco

Misfortune tests the sincerity of friends. 		 Do not attempt too much at once. 		 Score: 0.0986


Those who enter by the back stairs must not complain if they are thrown out by the window. 		 Two sureties are better than one. 		 Score: 0.0986


Those who practice deceit must expect to be shunned. 		 Happy is the man who learns from the misfortunes of others. 		 Score: 0.0984


Pride goes before destruction. 		 Those who are not able to roam should stay at home. 		 Score: 0.0984


The misfortunes arising from a man's own misconduct are the hardest to bear. 		 Two blacks do not make one white. 		 Score: 0.0984


The same measures will not suit all circumstances. 		 Misfortune tests the sincerity of friends. 		 Score: 0.0984


Do not attempt too much at once. 		 Those who stir up enmities are not to be trusted. 		 Score: 0.0984


The grateful heart will always find opportunities to show its gratitude. 		 A bird in the hand is worth two in the bush. 		 Score: 0.0983


No disguise will hide

One story is good, till another is told. 		 Change of habit cannot alter Nature. 		 Score: 0.0766


It is wise to turn circumstances to good account. 		 The value is in the worth, not in the number. 		 Score: 0.0766


The basest ingratitude is that which injures those who serve us. 		 Change not friends for foes. 		 Score: 0.0765


Look before you leap. 		 There is always some vulnerable part in the strongest armor. 		 Score: 0.0765


He who will steal a part will steal the whole. 		 Keep to your place, if you would succeed. 		 Score: 0.0765


If we nourish evil, it will sooner or later turn upon us. 		 Two blacks do not make one white. 		 Score: 0.0765


Distance exaggerates dangers. 		 Let every one stick to his own element. 		 Score: 0.0765


Whatever you do, do with all your might. 		 That which we are anxious to find, we are sometimes even more anxious to escape from, when we have succeeded in finding it. 		 Score: 0.0765


Everyone to his taste: one man's meat is another man's po

Do not attempt too much at once. 		 The grateful heart will always find opportunities to show its gratitude. 		 Score: 0.0478


Incentive spurs effort. 		 A man who talks for both sides is not to be trusted by either. 		 Score: 0.0477


Idleness brings want. 		 Avoid a remedy that is worse than the disease. 		 Score: 0.0476


When you seek to change your condition, be sure that you can better it. 		 Some men despise their best blessings because they come without cost. 		 Score: 0.0476


Happy is the man who learns from the misfortunes of others. 		 Avoid a remedy that is worse than the disease. 		 Score: 0.0475


We should not wait till a person is dead, to give him our respect. 		 Those who try to entrap others are sometimes caught by their own schemes. 		 Score: 0.0473


That which we are anxious to find, we are sometimes even more anxious to escape from, when we have succeeded in finding it. 		 He who slights his friends when they are not needed must not expect them to serve him whe

The grateful heart will always find opportunities to show its gratitude. 		 People are not to be judged by their coats. 		 Score: -0.0355


Those who stir up enmities are not to be trusted. 		 When you seek to change your condition, be sure that you can better it. 		 Score: -0.0358


Everyone has his trade. 		 Hypocritical speeches are easily seen through. 		 Score: -0.0367


Those who practice deceit must expect to be shunned. 		 A bird in the hand is worth two in the bush. 		 Score: -0.0371


Avoid a remedy that is worse than the disease. 		 If you wish to do a service, do it right. 		 Score: -0.0375


Avoid a remedy that is worse than the disease. 		 What is most truly valuable is often underrated. 		 Score: -0.0376


A man is known by the company he keeps. 		 Because we are like the great in one respect, we must not think we are like them in all. 		 Score: -0.0378


A man is known by the company he keeps. 		 No one is too weak to do good. 		 Score: -0.0380


Do not attempt too much

In [40]:
# Clustering

from sentence_transformers import SentenceTransformer
from sklearn.cluster import AgglomerativeClustering
import numpy as np

embedder = SentenceTransformer('all-MiniLM-L6-v2')

# Corpus with example sentences
corpus = morals
corpus_embeddings = embedder.encode(corpus)

# Normalize the embeddings to unit length
corpus_embeddings = corpus_embeddings /  np.linalg.norm(corpus_embeddings, axis=1, keepdims=True)

# Perform kmean clustering
clustering_model = AgglomerativeClustering(n_clusters=None, distance_threshold=1.5) #, affinity='cosine', linkage='average', distance_threshold=0.4)
clustering_model.fit(corpus_embeddings)
cluster_assignment = clustering_model.labels_

clustered_sentences = {}
for sentence_id, cluster_id in enumerate(cluster_assignment):
    if cluster_id not in clustered_sentences:
        clustered_sentences[cluster_id] = []

    clustered_sentences[cluster_id].append(corpus[sentence_id])

for i, cluster in clustered_sentences.items():
    print("Cluster ", i+1)
    print(cluster)
    print("")

Cluster  1
['Idleness brings want.', 'In quarreling about the shadow, we often lose the substance.', 'The poor and the weak are often made to suffer for the follies of the great.', 'Those who try to entrap others are sometimes caught by their own schemes.', 'The weak often revenge themselves on those who use them ill, even though they be the more powerful.', 'Those who practice cunning must expect to suffer by it.', 'We are encouraged by seeing others that are worse off than ourselves.', 'The lives of the idle can best be sacrificed.', 'Laziness often prepares a burden for its own back.', 'The desire for imaginary benefits often involves the loss of present blessings.', 'Those who strive are often watched by others who will take advantage of their defeat to benefit themselves', 'No one is too weak to do good.', 'Better be wise by the misfortunes of others than by your own.', 'Those who suffer most cry out the least.']

Cluster  10
['The perverse generally come to harm.', 'If we nourish

# Frame Net

In [31]:
data_cons = data_filt[data_filt.tag.apply(lambda x: x == "consequence")]
print(data_cons)

with open('aesopmorals_for_framing.txt', 'w', newline='') as f_output:
  
    for index, row in enumerate(data_cons['story']):
        f_output.write(row + "\n")

     Unnamed: 0                                                url  \
14           14  https://www.litscape.com/author/Aesop/The_Ass_...   
23           23  https://www.litscape.com/author/Aesop/The_Bird...   
56           56  https://www.litscape.com/author/Aesop/The_Dog_...   
58           58  https://www.litscape.com/author/Aesop/The_Dog_...   
82           82  https://www.litscape.com/author/Aesop/The_Fowl...   
85           85  https://www.litscape.com/author/Aesop/The_Fox_...   
92           92  https://www.litscape.com/author/Aesop/The_Fox_...   
102         102  https://www.litscape.com/author/Aesop/The_Goat...   
115         115  https://www.litscape.com/author/Aesop/The_Hen_...   
121         121  https://www.litscape.com/author/Aesop/The_Hors...   
157         157  https://www.litscape.com/author/Aesop/The_Monk...   
212         212  https://www.litscape.com/author/Aesop/The_Two_...   
217         217  https://www.litscape.com/author/Aesop/The_Vine...   
224         224  htt

## Word2vec

In [57]:
from nltk.corpus import stopwords
import nltk
import re
from keras.preprocessing.text import Tokenizer
from keras.preprocessing.sequence import pad_sequences
import gensim
W2V_PATH="GoogleNews-vectors-negative300.bin"
model_w2v = gensim.models.KeyedVectors.load_word2vec_format(W2V_PATH, binary=True)

documents_df=pandas.DataFrame(morals,columns=['documents'])

# removing special characters and stop words from the text
stop_words_l=stopwords.words('english')
documents_df['documents_cleaned']=documents_df.documents.apply(lambda x: " ".join(re.sub(r'[^a-zA-Z]',' ',w).lower() for w in x.split() if re.sub(r'[^a-zA-Z]',' ',w).lower() not in stop_words_l) )




[121 122 123   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0
   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0
   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0
   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0
   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0
   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0
   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0
   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0
   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0
   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0
   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0
   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0
   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0
   0   0   0   0   0   0   0   0   0   0   0   0   

In [64]:
from sklearn.feature_extraction.text import TfidfVectorizer 

tokenizer=Tokenizer()
tokenizer.fit_on_texts(documents_df.documents_cleaned)
tokenized_documents=tokenizer.texts_to_sequences(documents_df.documents_cleaned)
tokenized_paded_documents=pad_sequences(tokenized_documents,maxlen=64,padding='post')
vocab_size=len(tokenizer.word_index)+1
print (tokenized_paded_documents[0])

tfidfvectoriser=TfidfVectorizer()
tfidfvectoriser.fit(documents_df.documents_cleaned)
tfidf_vectors=tfidfvectoriser.transform(documents_df.documents_cleaned)

[121 122 123   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0
   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0
   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0
   0   0   0   0   0   0   0   0   0   0]
  (0, 459)	0.5773502691896258
  (0, 199)	0.5773502691896258
  (0, 56)	0.5773502691896258
  (1, 302)	0.5303315623621265
  (1, 182)	0.4894719719461459
  (1, 165)	0.4894719719461459
  (1, 73)	0.4894719719461459
  (2, 246)	0.35585675012012097
  (2, 225)	0.5395572176621449
  (2, 221)	0.5395572176621449
  (2, 76)	0.5395572176621449
  (3, 388)	0.4869243304355695
  (3, 363)	0.4869243304355695
  (3, 327)	0.4869243304355695
  (3, 283)	0.2945260269059221
  (3, 240)	0.44940906617983256
  (4, 427)	0.7348482321833306
  (4, 137)	0.6782315796665869
  (5, 394)	0.5921572105949618
  (5, 251)	0.5921572105949618
  (5, 70)	0.5465342403553395
  (6, 452)	0.1894837422055162
  (6, 407)	0.1894837422055162
  (6, 331)	0.1894837422055162
  (6, 307)	0.37896748

In [109]:
from sklearn.metrics.pairwise import cosine_similarity
from sklearn.metrics.pairwise import euclidean_distances


# creating embedding matrix, every row is a vector representation from the vocabulary indexed by the tokenizer index. 
embedding_matrix=np.zeros((vocab_size,300))
for word,i in tokenizer.word_index.items():
    if word in model_w2v:
        embedding_matrix[i]=model_w2v[word]
# creating document-word embeddings
document_word_embeddings=np.zeros((len(tokenized_paded_documents),64,300))
for i in range(len(tokenized_paded_documents)):
    for j in range(len(tokenized_paded_documents[0])):
        
        document_word_embeddings[i][j]=embedding_matrix[tokenized_paded_documents[i][j]]
print(document_word_embeddings.shape)

# calculating average of word vectors of a document weighted by tf-idf
document_embeddings=np.zeros((len(tokenized_paded_documents),300))
words=tfidfvectoriser.get_feature_names()
for i in range(len(document_word_embeddings)):
    for j in range(len(words)):
        document_embeddings[i]+=embedding_matrix[tokenizer.word_index[words[j]]]*tfidf_vectors[i, j]
        
        
def most_similar(doc_id,similarity_matrix,matrix):
    print (f'Document: {documents_df.iloc[doc_id]["documents"]}')
    print ('\n')
    print ('Similar Documents:')
    if matrix=='Cosine Similarity':
        similar_ix=np.argsort(similarity_matrix[doc_id])[::-1]
    elif matrix=='Euclidean Distance':
        similar_ix=np.argsort(similarity_matrix[doc_id])
    for ix in similar_ix[0:10]:
        if ix==doc_id:
            continue
        print('\n')
        print (f'Document: {documents_df.iloc[ix]["documents"]}')
        print (f'{matrix} : {similarity_matrix[doc_id][ix]}')

pairwise_similarities=cosine_similarity(document_embeddings)
pairwise_differences=euclidean_distances(document_embeddings)
most_similar(1,pairwise_similarities,'Cosine Similarity')

(141, 64, 300)


C:\Users\Thiloshon\.conda\envs\yt\lib\site-packages\sklearn\utils\deprecation.py:87: FutureWarning: Function get_feature_names is deprecated; get_feature_names is deprecated in 1.0 and will be removed in 1.2. Please use get_feature_names_out instead.
  warnings.warn(msg, category=FutureWarning)


Document: The perverse generally come to harm.


Similar Documents:


Document: Harm hatch, harm catch.
Cosine Similarity : 0.6046173987276067


Document: Do nothing without a regard to the consequences.
Cosine Similarity : 0.5979411721310954


Document: Men of evil reputation, when they perform a good deed, fail to get credit for it.
Cosine Similarity : 0.5652038393703975


Document: Whatever you do, do with all your might.
Cosine Similarity : 0.5640008494051171


Document: Inconsiderate and ill-matched alliances generally end in ruin; and the man who compasses the destruction of his neighbor is often caught in his own snare.
Cosine Similarity : 0.5619046146453462


Document: Sweet words may deliver us from peril, when harsh words would fail.
Cosine Similarity : 0.5481161431974961


Document: Those who practice cunning must expect to suffer by it.
Cosine Similarity : 0.5478641338989125


Document: Because we are like the great in one respect, we must not think we are like them in all.